In [1]:
import numpy as np
import pandas as pd
import tqdm
from sklearn.model_selection import train_test_split
import torch
import torch.nn as nn
from torch.utils.data import DataLoader, RandomSampler, SequentialSampler
from transformers import TrainingArguments, Trainer
from transformers import BartTokenizer, BartForConditionalGeneration, EarlyStoppingCallback
import ray
from ray import tune
from ray.tune.suggest.hyperopt import *
from ray.tune.schedulers import *
from time import time

device = torch.device("cuda")
print('GPU:', torch.cuda.get_device_name())

GPU: A100-SXM4-40GB


In [2]:
# load model and tokenizer
model_name = "facebook/bart-large-cnn"
tokenizer = BartTokenizer.from_pretrained(model_name)

# load tokenized train/dev data
train_source_tokenized  = torch.load('20_train_source_tokenized.pt')
train_target_tokenized  = torch.load('20_train_target_tokenized.pt')
dev_source_tokenized  = torch.load('20_dev_source_tokenized.pt')
dev_target_tokenized  = torch.load('20_dev_target_tokenized.pt')

In [3]:
# custom dataset class for data loading
class CustomDataset(torch.utils.data.Dataset):
    def __init__(self, source, target):
        self.source = source
        self.target = target

    def __getitem__(self, idx):
        target = {key: torch.tensor(val[idx]) for key, val in self.target.items()}
        target_input_ids = target['input_ids'][:-1].detach().clone()
        target_attention_mask = target['attention_mask'][:-1].detach().clone()

        labels = target['input_ids'][1:].detach().clone()
        labels[labels[:] == tokenizer.pad_token_id] = -100

        source = {key: torch.tensor(val[idx]) for key, val in self.source.items()}
        
        item = {'input_ids': source['input_ids'].detach().clone(),
                'attention_mask': source['attention_mask'].detach().clone(),
                'decoder_input_ids': target_input_ids.detach().clone(),
                'decoder_attention_mask': target_attention_mask.detach().clone(),
                'labels': labels}

        return item

    def __len__(self):
        return len(self.source["input_ids"])

train_dataset = CustomDataset(train_source_tokenized, train_target_tokenized)
val_dataset = CustomDataset(dev_source_tokenized, dev_target_tokenized)

In [4]:
# arguments for Huggingface trainer class
args = TrainingArguments(
    num_train_epochs=3,
    per_device_train_batch_size=10,
    per_device_eval_batch_size=10,
    output_dir="output",
    evaluation_strategy = "steps",
    eval_steps = 250,
    save_strategy = "no",
    metric_for_best_model = 'eval_loss',
    load_best_model_at_end=True,
    fp16 = True
    )

# model initialization function for each trial of HP search
def model_init():
    model = BartForConditionalGeneration.from_pretrained("facebook/bart-large-cnn")
    for param in model.base_model.encoder.parameters():
        param.requires_grad = False
    for param in model.base_model.shared.parameters():
        param.requires_grad = False
    return model    

trainer = Trainer(
    model_init = model_init,
    args=args,
    train_dataset=train_dataset,
    eval_dataset=val_dataset,
    callbacks=[EarlyStoppingCallback(early_stopping_patience = 2)])

# Hyperparameter tuning
def hp_space_ray(trial):
    return {
        "learning_rate": tune.loguniform(1e-6, 1e-3),
        "weight_decay": tune.uniform(0.001,0.1),
        "seed": tune.choice(range(1, 41)),
        }

best_trial = trainer.hyperparameter_search(
    hp_space = hp_space_ray,
    n_trials=10, 
    direction="minimize",
    backend="ray",
    resources_per_trial={"cpu": 96, "gpu": 8}
    )

2021-04-04 00:11:28,971	INFO services.py:1174 -- View the Ray dashboard at http://127.0.0.1:8265
2021-04-04 00:11:38,729	WARNING function_runner.py:541 -- Function checkpointing is disabled. This may result in unexpected behavior when using checkpointing features or certain schedulers. To enable, set the train function arguments to be `func(config, checkpoint_dir=None)`.


== Status ==
Memory usage on this node: 25.7/1121.8 GiB
Using FIFO scheduling algorithm.
Resources requested: 96/96 CPUs, 8/8 GPUs, 0.0/914.7 GiB heap, 0.0/128.52 GiB objects
Result logdir: /home/ubuntu/ray_results/_inner_2021-04-04_00-11-38
Number of trials: 1/10 (1 RUNNING)
+--------------------+----------+-------+-----------------+--------+----------------+
| Trial name         | status   | loc   |   learning_rate |   seed |   weight_decay |
|--------------------+----------+-------+-----------------+--------+----------------|
| _inner_53789_00000 | RUNNING  |       |     1.32929e-05 |     12 |      0.0951207 |
+--------------------+----------+-------+-----------------+--------+----------------+




(pid=4929) /home/ubuntu/anaconda3/envs/pytorch_latest_p37/lib/python3.7/site-packages/ray/workers/default_worker.py:7: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
(pid=4929)   
(pid=4929) /home/ubuntu/anaconda3/envs/pytorch_latest_p37/lib/python3.7/site-packages/ray/workers/default_worker.py:14: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
(pid=4929)   from ray.ray_logging import get_worker_log_file_name, configure_log_file
(pid=4929) /home/ubuntu/anaconda3/envs/pytorch_latest_p37/lib/python3.7/site-packages/torch/nn/parallel/_functions.py:65: UserWarning: Was asked to gather along dimension 0, but all input tensors were scalars; will instead unsqueeze and return a vector.
(pid=4929)   wa

(pid=4929) <IPython.core.display.HTML object>
(pid=4929) <IPython.core.display.HTML object>
(pid=4929) <IPython.core.display.HTML object>
(pid=4929) <IPython.core.display.HTML object>
(pid=4929) <IPython.core.display.HTML object>
(pid=4929) <IPython.core.display.HTML object>
(pid=4929) <IPython.core.display.HTML object>
(pid=4929) <IPython.core.display.HTML object>
(pid=4929) <IPython.core.display.HTML object>
(pid=4929) <IPython.core.display.HTML object>
(pid=4929) <IPython.core.display.HTML object>
(pid=4929) <IPython.core.display.HTML object>
(pid=4929) <IPython.core.display.HTML object>
(pid=4929) <IPython.core.display.HTML object>
(pid=4929) <IPython.core.display.HTML object>
(pid=4929) <IPython.core.display.HTML object>
(pid=4929) <IPython.core.display.HTML object>
(pid=4929) <IPython.core.display.HTML object>
(pid=4929) <IPython.core.display.HTML object>
(pid=4929) <IPython.core.display.HTML object>
(pid=4929) <IPython.core.display.HTML object>
(pid=4929) <IPython.core.display.H

(pid=4929) /home/ubuntu/anaconda3/envs/pytorch_latest_p37/lib/python3.7/site-packages/ray/workers/default_worker.py:7: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
(pid=4929)   
(pid=4929) /home/ubuntu/anaconda3/envs/pytorch_latest_p37/lib/python3.7/site-packages/ray/workers/default_worker.py:14: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
(pid=4929)   from ray.ray_logging import get_worker_log_file_name, configure_log_file
(pid=4929) /home/ubuntu/anaconda3/envs/pytorch_latest_p37/lib/python3.7/site-packages/torch/nn/parallel/_functions.py:65: UserWarning: Was asked to gather along dimension 0, but all input tensors were scalars; will instead unsqueeze and return a vector.
(pid=4929)   wa

...

(pid=5014) <IPython.core.display.HTML object>
(pid=5014) <IPython.core.display.HTML object>
(pid=5014) <IPython.core.display.HTML object>
(pid=5014) <IPython.core.display.HTML object>
(pid=5014) <IPython.core.display.HTML object>
(pid=5014) <IPython.core.display.HTML object>
(pid=5014) <IPython.core.display.HTML object>
(pid=5014) <IPython.core.display.HTML object>
(pid=5014) <IPython.core.display.HTML object>
(pid=5014) <IPython.core.display.HTML object>
(pid=5014) <IPython.core.display.HTML object>
(pid=5014) <IPython.core.display.HTML object>
(pid=5014) <IPython.core.display.HTML object>
(pid=5014) <IPython.core.display.HTML object>
(pid=5014) <IPython.core.display.HTML object>
(pid=5014) <IPython.core.display.HTML object>
(pid=5014) <IPython.core.display.HTML object>
(pid=5014) <IPython.core.display.HTML object>
(pid=5014) <IPython.core.display.HTML object>
(pid=5014) <IPython.core.display.HTML object>
(pid=5014) <IPython.core.display.HTML object>
(pid=5014) <IPython.core.display.H

(pid=5014) /home/ubuntu/anaconda3/envs/pytorch_latest_p37/lib/python3.7/site-packages/ray/workers/default_worker.py:7: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
(pid=5014)   
(pid=5014) /home/ubuntu/anaconda3/envs/pytorch_latest_p37/lib/python3.7/site-packages/ray/workers/default_worker.py:14: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
(pid=5014)   from ray.ray_logging import get_worker_log_file_name, configure_log_file
(pid=5014) /home/ubuntu/anaconda3/envs/pytorch_latest_p37/lib/python3.7/site-packages/torch/nn/parallel/_functions.py:65: UserWarning: Was asked to gather along dimension 0, but all input tensors were scalars; will instead unsqueeze and return a vector.
(pid=5014)   wa

(pid=5014) <IPython.core.display.HTML object>
(pid=5014) <IPython.core.display.HTML object>
(pid=5014) <IPython.core.display.HTML object>
(pid=5014) <IPython.core.display.HTML object>
(pid=5014) <IPython.core.display.HTML object>
(pid=5014) <IPython.core.display.HTML object>
(pid=5014) <IPython.core.display.HTML object>
(pid=5014) <IPython.core.display.HTML object>
(pid=5014) <IPython.core.display.HTML object>
(pid=5014) <IPython.core.display.HTML object>
(pid=5014) <IPython.core.display.HTML object>
(pid=5014) <IPython.core.display.HTML object>
(pid=5014) <IPython.core.display.HTML object>
(pid=5014) <IPython.core.display.HTML object>
(pid=5014) <IPython.core.display.HTML object>
(pid=5014) <IPython.core.display.HTML object>
(pid=5014) <IPython.core.display.HTML object>
(pid=5014) <IPython.core.display.HTML object>
(pid=5014) <IPython.core.display.HTML object>
(pid=5014) <IPython.core.display.HTML object>
(pid=5014) <IPython.core.display.HTML object>
(pid=5014) <IPython.core.display.H

2021-04-04 06:48:24,016	INFO tune.py:450 -- Total run time: 23816.31 seconds (23805.07 seconds for the tuning loop).


Result for _inner_53789_00009:
  date: 2021-04-04_06-47-59
  done: true
  eval_loss: 1.7463024854660034
  eval_runtime: 85.7473
  eval_samples_per_second: 233.243
  experiment_id: 5a1ec22fa5fd43a8b8afebeb27ff0d4f
  experiment_tag: 9_learning_rate=1.9762e-05,seed=21,weight_decay=0.029832
  hostname: ip-172-31-38-128
  iterations_since_restore: 10
  node_ip: 172.31.38.128
  objective: 1.7463024854660034
  pid: 5014
  time_since_restore: 2257.367800951004
  time_this_iter_s: 219.16746282577515
  time_total_s: 2257.367800951004
  timestamp: 1617518879
  timesteps_since_restore: 0
  training_iteration: 10
  trial_id: '53789_00009'
  
== Status ==
Memory usage on this node: 36.3/1121.8 GiB
Using FIFO scheduling algorithm.
Resources requested: 0/96 CPUs, 0/8 GPUs, 0.0/914.7 GiB heap, 0.0/128.52 GiB objects
Result logdir: /home/ubuntu/ray_results/_inner_2021-04-04_00-11-38
Number of trials: 10/10 (10 TERMINATED)
+--------------------+------------+-------+-----------------+--------+------------

In [ ]:
# +--------------------+------------+-------+-----------------+--------+----------------+-------------+
# | Trial name         | status     | loc   |   learning_rate |   seed |   weight_decay |   objective |
# |--------------------+------------+-------+-----------------+--------+----------------+-------------|
# | _inner_53789_00000 | TERMINATED |       |     1.32929e-05 |     12 |      0.0951207 |     1.75128 |
# | _inner_53789_00001 | TERMINATED |       |     0.00015703  |      9 |      0.0602672 |     1.84101 |
# | _inner_53789_00002 | TERMINATED |       |     2.93803e-06 |     30 |      0.0164435 |     1.82803 |
# | _inner_53789_00003 | TERMINATED |       |     1.49366e-06 |     28 |      0.0867514 |     1.87127 |
# | _inner_53789_00004 | TERMINATED |       |     6.35836e-05 |     36 |      0.0710992 |     1.76525 |
# | _inner_53789_00005 | TERMINATED |       |     1.1528e-06  |      4 |      0.0970211 |     1.88852 |
# | _inner_53789_00006 | TERMINATED |       |     0.000314288 |     17 |      0.0220216 |     2.0415  |
# | _inner_53789_00007 | TERMINATED |       |     3.51136e-06 |      2 |      0.019157  |     1.81678 |
# | _inner_53789_00008 | TERMINATED |       |     8.1795e-06  |      9 |      0.0529509 |     1.77046 |
# | _inner_53789_00009 | TERMINATED |       |     1.97622e-05 |     21 |      0.0298317 |     1.7463  |
# +--------------------+------------+-------+-----------------+--------+----------------+-------------+